# Demo notebook for swctools basic functionality

I have included a couple `swc` files in `data/swc` to demonstrate the basic functionality of the package.

In [1]:
from pathlib import Path
from swctools import *

swc_filepath = Path("../data/swc/TS2_s50.swc")
ps_filepath = Path("../data/points/TS2_AZ.txt")

First, let's load a SWC file and parse it using the io module.

In [2]:
parse = parse_swc(swc_filepath)
print(parse)

SWCParseResult(records=16, reconnections=1, comments=5)


We can create a `SWCModel` from the parse result.

In [3]:
swc = SWCModel.from_parse_result(parse)
swc.print_attributes()

SWCModel: nodes=16, edges=15, components=1, cycles=0, branch_points=1, roots=1, leaves=2, self_loops=0, density=0.1250


Instead of working with `io` directly, we can create a `SWCModel` from a SWC file.

In [4]:
swc = SWCModel.from_swc_file(swc_filepath)
swc.print_attributes(node_info=True, edge_info=True)

SWCModel: nodes=16, edges=15, components=1, cycles=0, branch_points=1, roots=1, leaves=2, self_loops=0, density=0.1250
Nodes:
  1: t=3, x=8878.525222, y=2745.038908, z=2262.158844, r=11.653035, line=6
  2: t=3, x=8884.305343, y=2735.691509, z=2310.776616, r=19.378935, line=7
  3: t=3, x=8886.497449, y=2742.173531, z=2359.738246, r=25.623099, line=8
  4: t=3, x=8879.841132, y=2761.238472, z=2405.241298, r=29.852547, line=9
  5: t=3, x=8867.051941, y=2790.856973, z=2442.859475, r=37.62364, line=10
  6: t=3, x=8845.80538, y=2816.782558, z=2479.936126, r=61.436812, line=11
  7: t=3, x=8834.940118, y=2832.446277, z=2524.050036, r=76.826678, line=12
  8: t=3, x=8842.115732, y=2832.605614, z=2561.570012, r=60.985865, line=13
  9: t=3, x=8871.116979, y=2821.242856, z=2593.890695, r=20.372681, line=14
  10: t=3, x=8851.063224, y=2821.001451, z=2638.232454, r=43.704201, line=15
  11: t=3, x=8853.39809, y=2816.419776, z=2650.603399, r=47.086212, line=16
  12: t=3, x=8859.06809, y=2796.68527, z=26

We want to represent the model as a general graph with nodes and edges rather than a tree. For this we use the `GeneralModel` class.

In [5]:
gm = GeneralModel.from_swc_file(swc_filepath)
gm.print_attributes(node_info=True, edge_info=True)

GeneralModel: nodes=15, edges=15, components=1, cycles=1, branch_points=2, leaves=2, self_loops=0, density=0.1429
Nodes:
  1: n=1, x=8878.525222, y=2745.038908, z=2262.158844, r=11.653035, t=3, merged_ids=[1], lines=[6]
  2: n=2, x=8884.305343, y=2735.691509, z=2310.776616, r=19.378935, t=3, merged_ids=[2], lines=[7]
  3: n=3, x=8886.497449, y=2742.173531, z=2359.738246, r=25.623099, t=3, merged_ids=[3], lines=[8]
  4: n=4, x=8879.841132, y=2761.238472, z=2405.241298, r=29.852547, t=3, merged_ids=[4], lines=[9]
  5: n=5, x=8867.051941, y=2790.856973, z=2442.859475, r=37.62364, t=3, merged_ids=[5], lines=[10]
  6: n=6, x=8845.80538, y=2816.782558, z=2479.936126, r=61.436812, t=3, merged_ids=[6], lines=[11]
  7: n=7, x=8834.940118, y=2832.446277, z=2524.050036, r=76.826678, t=3, merged_ids=[7], lines=[12]
  8: n=8, x=8842.115732, y=2832.605614, z=2561.570012, r=60.985865, t=3, merged_ids=[8, 16], lines=[13, 21]
  9: n=9, x=8871.116979, y=2821.242856, z=2593.890695, r=20.372681, t=3, merg

## Visualization

We have a `GeneralModel` and we want to visualize it. We can use the `plot_centroid` function to visualize the skeleton of the model.

In [6]:
fig_centroid = plot_centroid(gm, show_nodes=True)
fig_centroid.show()

SWC models are often constructed as a set of frusta in simulation codes. For this we have the `FrustaSet` class, which can be created from a `GeneralModel`. A `FrustaSet` can be visualized using the `plot_frusta` function.

In [7]:
frusta = FrustaSet.from_general_model(gm, sides=20, end_caps=True)
fig_frusta = plot_frusta(frusta)
fig_frusta.show()

A very useful feature of `plot_frusta_slider` function is the ability to change the radius of the frusta interactively.

In [8]:
frusta = FrustaSet.from_general_model(gm, sides=20, end_caps=False)
fig_frusta = plot_frusta_slider(frusta)
fig_frusta.show()

If we want to overlay the frusta with the centroid skeleton, we can use the `plot_frusta_with_centroid` function.

In [9]:
plot_frusta_with_centroid(gm, frusta, show_nodes=True)

From these individual functions, we can build a more comprehensive visualization functionality using the `plot_model` function. This allows for a more interactive and dynamic visualization of the combined centroid skeleton and frusta mesh, and also includes the option to plot a set of points as little spheres.

In [10]:
plot_model(gm=gm, frusta=frusta, slider=True)

Our `geometry` module includes a class `PointSet` for batched spheres at arbitrary xyz points.

In [11]:
ps = PointSet.from_txt(ps_filepath)

fig = plot_model(
    gm=gm,
    frusta=frusta,
    show_frusta=True,
    show_centroid=True,
    slider=True,
    point_set=ps,  # use the PointSet
    point_size=5,  # multiplies base_radius (0.05 * 1.5 = 0.075)
    point_color="crimson",
)
fig.show()